In [ ]:
# korecipegpt_kernel
# fine-tuning with pulmu1 dataset
# specifically, pulmu1 csv dataset to qa dataset/json file

In [3]:
%%capture

%pip install openpyxl

In [18]:
import pandas as pd

# 엑셀 파일의 경로
file_path = '/home/jaesung/pulmuone/instruction_tuning_2/v4_completion/data/pulmu1_dataset_v3.xlsx'

# 모든 시트를 로드하고 결합하는 함수
def load_and_concat_sheets(file_path):
    # 엑셀 파일의 모든 시트를 딕셔너리 형태로 로드
    all_sheets = pd.read_excel(file_path, sheet_name=None)
    
    # 모든 시트의 데이터를 담을 리스트
    frames = []
    
    # 각 시트의 데이터를 리스트에 추가
    for sheet_name, data in all_sheets.items():
        data['SheetName'] = sheet_name  # 각 데이터프레임에 시트 이름 열 추가 (선택사항)
        frames.append(data)
    
    # 모든 데이터를 하나의 데이터프레임으로 결합
    result = pd.concat(frames, ignore_index=True)
    
    return result

# 엑셀 파일 로드 및 결합
combined_df = load_and_concat_sheets(file_path)
print(combined_df.head())  # 결합된 데이터프레임의 첫 5행 출력

          REG_NO  item_id item_nm food_typ_cd food_typ_nm open_yn  reg_id  \
0  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   
1  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   
2  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   
3  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   
4  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   

  emp_nm  dept_nm  dept_id  ...                        origins  prnt_id  \
0    박주헌  CTO_BI팀    10203  ...                            국산.        0   
1    박주헌  CTO_BI팀    10203  ...                            국내산        0   
2    박주헌  CTO_BI팀    10203  ...                            국내산        0   
3    박주헌  CTO_BI팀    10203  ...  국내제조[옥수수:외국산(러시아,헝가리,세르비아,등)]        0   
4    박주헌  CTO_BI팀    10203  ...                             국산        0   

   contents               reg_dt               mod_dt             reg_dt_1  \
0   62.1

In [19]:
%%capture

# %pip install scikit-learn
# %pip install -U sentence-transformers

In [20]:
import copy

df = copy.deepcopy(combined_df)

In [21]:
def get_non_zero_columns(pivot_df):
    non_zero_columns = {}
    for index, row in pivot_df.iterrows():
        non_zero_columns[index] = row[row != 0].index.tolist()
    return non_zero_columns

In [22]:
item_mat_df = pd.pivot_table(df, values='contents', index='item_nm', columns='mat_nm', fill_value=0)

item_mat_dict= get_non_zero_columns(item_mat_df)

In [23]:
df.head(2)

REG_NO  item_id item_nm food_typ_cd food_typ_nm open_yn  reg_id  \
0  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   
1  MI-230307-016     7353    관절청춘         NaN      건강기능식품       Y  139199   

  emp_nm  dept_nm  dept_id  ... origins  prnt_id  contents  \
0    박주헌  CTO_BI팀    10203  ...     국산.        0   62.1984   
1    박주헌  CTO_BI팀    10203  ...     국내산        0   13.0000   

                reg_dt               mod_dt             reg_dt_1  \
0  2023-03-07 13:55:25  2023-03-07 13:55:25  2023-03-07 13:44:50   
1  2023-03-07 13:56:34  2023-03-07 13:56:34  2023-03-07 13:44:50   

  fn_level(A.reg_no, B.prnt_id) ing_typ_nm  br_food_category  SheetName  
0                            1차          -           건강기능성제품     Sheet1  
1                            1차       올리고당           건강기능성제품     Sheet1  

[2 rows x 27 columns]

In [24]:
df.columns

Index(['REG_NO', 'item_id', 'item_nm', 'food_typ_cd', 'food_typ_nm', 'open_yn',
       'reg_id', 'emp_nm', 'dept_nm', 'dept_id', 'reg_no.1', 'seq_no',
       'sply_id', 'sply_nm', 'DEL_YN', 'mat_id', 'mat_nm', 'origins',
       'prnt_id', 'contents', 'reg_dt', 'mod_dt', 'reg_dt_1',
       'fn_level(A.reg_no, B.prnt_id)', 'ing_typ_nm', 'br_food_category',
       'SheetName'],
      dtype='object')

In [25]:
import pandas as pd

# 예제 데이터프레임 (이미지 내용을 기반으로)
data = {
    'item_nm': list(df['item_nm']),
    'SheetName': list(df['SheetName']),
    'origins': list(df['origins']),
    'food_typ_nm': list(df['food_typ_nm']),
    'ing_typ_nm': list(df['ing_typ_nm']),
    'mat_nm': list(df['mat_nm']),
}

df = pd.DataFrame(data)

# 'item_nm'으로 그룹화
grouped = df.groupby('item_nm').agg({
    'SheetName': 'first',
    'origins': lambda x: list(x),
    'food_typ_nm': 'first',  # food_typ_nm은 동일한 값을 가질 경우 first()를 사용하여 문자열로 반환
    'ing_typ_nm': lambda x: list(x),  # ing_typ_nm은 리스트로 반환
    'mat_nm': lambda x: list(x),
}).reset_index()

In [26]:
grouped.head()

item_nm SheetName                                            origins  \
0      '23김치생수제비    Sheet1  [호주산, 국내가공(밀:호주,미국), 태국산, 태국산, 국산, 중국산, 국산, 중국...   
1   '23맑은소고기어묵전골    Sheet1  [국내산, 국산, 국내산, 국산, 국산, 미국산, 국내산, 국산, 리투아니아, 태국...   
2      '23물냉면밀키트    Sheet1  [밀:미국산,호주산, 국내제조, 국내제조, 국내, 국내산, 국산, 중국산, 태국산,...   
3   '23진한가쓰오어묵전골    Sheet1  [국내산, 국산, 국내산, 국산, 국산, 미국산, 미국산, 국내산, 국산, 리투아니...   
4  '23풀스키즈_사각쑥절편    Sheet1                        [국산, 국내산, 국산, 국산, 국내제조, 국산]   

  food_typ_nm                                         ing_typ_nm  \
0    생면주정처리제품  [밀가루　, 밀가루, 식품첨가물(혼합제제), 식품첨가물(화학적합성품), 주정, 곡류...   
1          어묵  [식용유지, 일반식품기타가공품, 정제소금, 채소류, 농산물, 두류가공품, 농산물, ...   
2      숙면주정처리  [밀가루, 전분가공품, 곡류, 비공개, 곡류, 정제염, 곡류가공품, 일반가공식품(전...   
3          어묵  [식용유지, 일반식품기타가공품, 정제소금, 채소류, 농산물, 연육, 두류가공품, 농...   
4          떡류                [농산물, 기타가공품, 재제소금, 기타가공품, 대두유, 정제수]   

                                              mat_nm  
0  [밀가루, 밀가루, 변성전분sa2, 변성전분pn, 주정, 밀글루텐, 정제소금, 알파...  
1  [대두유, 유산균배양액혼합분말, 정제염, 마늘, 양파, 대두단백, 고추, 정백당, ...  
2  [소맥분, 고구마전분, 혼합메밀가루, 주정, 흑미가루, 정제소금, 도토리가루, 타피...  
3  [대두유, 유산균배양액혼합분말, 정제염, 마늘, 양파, 연육명태a, 대두단백, 고추...  
4                    [멥쌀, 냉동쑥, 한주꽃소금, 쑥가루, 대두유, 정제수]

In [27]:
len(grouped)

3419

In [28]:
# 등장 횟수 계산
from collections import Counter

grouped['mat_nm']
res = []
for v in grouped['mat_nm']:
    res.extend(v)

def count_elements(lst):
    return dict(Counter(lst))

ing_freqeuncy_dict = count_elements(res)

In [32]:
def classify_elements(count_dict):
    core_threshold = 1
    general_threshold_min = 2
    general_threshold_max = 5
    common_threshold_min = 6
    common_threshold_max = 20

    core_elements = {key: val for key, val in count_dict.items() if val == core_threshold}
    general_elements = {key: val for key, val in count_dict.items() if general_threshold_min <= val <= general_threshold_max}
    common_elements = {key: val for key, val in count_dict.items() if common_threshold_min <= val <= common_threshold_max}
    very_common_elements = {key: val for key, val in count_dict.items() if val > common_threshold_max}

    return core_elements, general_elements, common_elements, very_common_elements

core_ing, general_ing, common_ing, very_common_ing = classify_elements(ing_freqeuncy_dict)


In [34]:
# 'item_nm'을 key로, 나머지 컬럼을 value로 가지는 딕셔너리 생성
side_info_dict = grouped.set_index('item_nm').T.to_dict()

In [35]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

model = SentenceTransformer('bespin-global/klue-sroberta-base-continue-learning-by-mnr')

/home/jaesung/anaconda3/envs/alpaca/lib/python3.12/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange
/home/jaesung/anaconda3/envs/alpaca/lib/python3.12/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [36]:
def similar_topn(item_str, ing_list, n):
    # 예제 식재료 리스트
    ingredients =  ing_list # ['ing1', 'ing2', ..]
    # 비교할 식품명
    food_name = item_str # item_nm

    # 임베딩 벡터 생성
    food_embedding = model.encode(food_name)
    ingredient_embeddings = {ingredient: model.encode(ingredient) for ingredient in ingredients}

    # 코사인 유사도 계산
    similarities = {}
    for ingredient, embedding in ingredient_embeddings.items():
        sim = cosine_similarity([food_embedding], [embedding])[0][0]
        similarities[ingredient] = sim

    # 유사도가 큰 순서대로 정렬하여 가장 유사한 식재료 2~3개 선택
    most_similar_ingredients = sorted(similarities, key=similarities.get, reverse=True)[:n]

    # print(f"'{food_name}'와(과) 가장 유사한 식재료는: {most_similar_ingredients}")

    return food_name, most_similar_ingredients

In [37]:
def similar_topnpercent(item_str, ing_list, percent):
    # 예제 식재료 리스트
    ingredients =  ing_list # ['ing1', 'ing2', ..]
    # 비교할 식품명
    food_name = item_str # item_nm

    # 임베딩 벡터 생성
    food_embedding = model.encode(food_name)
    ingredient_embeddings = {ingredient: model.encode(ingredient) for ingredient in ingredients}

    # 코사인 유사도 계산
    similarities = {}
    for ingredient, embedding in ingredient_embeddings.items():
        sim = cosine_similarity([food_embedding], [embedding])[0][0]
        similarities[ingredient] = sim

    # 유사도가 큰 순서대로 정렬하여 가장 유사한 식재료 30% 선택
    n = int(len(ingredients) * percent)

    most_similar_ingredients = sorted(similarities, key=similarities.get, reverse=True)[:n]

    # print(f"'{food_name}'와(과) 가장 유사한 식재료는: {most_similar_ingredients}")

    return food_name, most_similar_ingredients

In [70]:
topn_dict = {}
for i, (k, v) in enumerate(item_mat_dict.items()):
    # food_nm, topn= similar_topn(k, v, 3)
    food_nm, topn= similar_topnpercent(k, v, 0.2)
    topn_dict[food_nm] = topn

In [38]:
def classify_new_list(new_list, core_elements, general_elements, common_elements, very_common_elements):
    new_core = []
    new_general = []
    new_common = []
    new_very_common = []

    for item in new_list:
        if item in core_elements:
            new_core.append(item)
        elif item in general_elements:
            new_general.append(item)
        elif item in common_elements:
            new_common.append(item)
        elif item in very_common_elements:
            new_very_common.append(item)
        else:
            # 해당하지 않는 원소는 처리하지 않거나 다른 리스트에 추가할 수 있음
            pass

    return new_core, new_general, new_common, new_very_common

In [39]:
import random
import math

def exclude_30_percent_elements(list1, list2, list3, list4):
    def exclude_elements(lst):
        exclude_count = math.ceil(len(lst) * 0.3)
        exclude_indices = random.sample(range(len(lst)), exclude_count)
        excluded_elements = [lst[i] for i in exclude_indices]
        remaining_elements = [lst[i] for i in range(len(lst)) if i not in exclude_indices]
        return remaining_elements, excluded_elements

    remaining1, excluded1 = exclude_elements(list1)
    remaining2, excluded2 = exclude_elements(list2)
    remaining3, excluded3 = exclude_elements(list3)
    remaining4, excluded4 = exclude_elements(list4)

    all_excluded = excluded1 + excluded2 + excluded3 + excluded4

    return remaining1, remaining2, remaining3, remaining4, all_excluded


In [40]:
# sample prompt

cnt = 0
for (k, all_ing), (k, side_info), (k, three_ing) in zip(item_mat_dict.items(), side_info_dict.items(), topn_dict.items()):
    remain_ing = [ing for ing in all_ing if ing not in three_ing]
    
    # 기존 분류에 very_common을 추가
    new_core_ing, new_general_ing, new_common_ing, new_very_common_ing = classify_new_list(all_ing, core_ing, general_ing, common_ing, very_common_ing)
    
    print(k)
    print(all_ing)
    print(new_core_ing)
    print(new_general_ing)
    print(new_common_ing)
    print(new_very_common_ing)
    print(side_info['food_typ_nm'])
    print('')
    
    # exclude_30_percent_elements 함수도 very_common_ing을 추가하여 호출
    remaining_core_ing, remaining_general_ing, remaining_common_ing, remaining_very_common_ing, excluded = exclude_30_percent_elements(new_core_ing, new_general_ing, new_common_ing, new_very_common_ing)
    
    if len(three_ing) > 0:
        instruction_data = {
            "instruction": f"다음은 {k}의 식재료의 일부입니다. 빠진 식재료를 맞추세요.",
            "input": f"핵심 재료: \"{', '.join(remaining_core_ing)}\"\n일반 재료: \"{', '.join(remaining_general_ing)}\"\n공통 재료: \"{', '.join(remaining_common_ing)}\"\n매우 자주 등장하는 재료: \"{', '.join(remaining_very_common_ing)}\"",
            "output": ", ".join(excluded)
        }
        
    print(instruction_data)
    
    cnt += 1
    if cnt > 0:
        break



NameError: name 'topn_dict' is not defined

In [41]:
import json

def transform_dict_to_qa_format(item_dict, side_dict):
    qa_list = []
    for (k, all_ing), (k, side_info) in zip(item_dict.items(), side_dict.items()):
        # 기존 classify_new_list에 very_common_ing을 추가
        new_core_ing, new_general_ing, new_common_ing, new_very_common_ing = classify_new_list(all_ing, core_ing, general_ing, common_ing, very_common_ing)
        
        # 기존 exclude_30_percent_elements에 very_common_ing을 추가
        remaining_core_ing1, remaining_general_ing1, remaining_common_ing1, remaining_very_common_ing1, excluded1 = exclude_30_percent_elements(new_core_ing, new_general_ing, new_common_ing, new_very_common_ing)
        remaining_core_ing2, remaining_general_ing2, remaining_common_ing2, remaining_very_common_ing2, excluded2 = exclude_30_percent_elements(new_core_ing, new_general_ing, new_common_ing, new_very_common_ing)
        remaining_core_ing3, remaining_general_ing3, remaining_common_ing3, remaining_very_common_ing3, excluded3 = exclude_30_percent_elements(new_core_ing, new_general_ing, new_common_ing, new_very_common_ing)
        remaining_core_ing4, remaining_general_ing4, remaining_common_ing4, remaining_very_common_ing4, excluded4 = exclude_30_percent_elements(new_core_ing, new_general_ing, new_common_ing, new_very_common_ing)
        
        # 다양한 질문 형식을 생성
        questions = [
            {
                "instruction": f"{side_info['food_typ_nm']} 카테고리의 {k}의 식재료의 일부입니다. 빠진 식재료를 맞추세요.",
                "input": f"핵심 재료: \"{', '.join(remaining_core_ing1)}\"\n일반 재료: \"{', '.join(remaining_general_ing1)}\"\n공통 재료: \"{', '.join(remaining_common_ing1)}\"\n매우 자주 등장하는 재료: \"{', '.join(remaining_very_common_ing1)}\"",
            },
            {
                "instruction": f"{side_info['food_typ_nm']} 카테고리에 속하는 {k}의 일부 재료가 주어졌습니다. 나머지 식재료를 추측해보세요.",
                "input": f"핵심 재료: \"{', '.join(remaining_core_ing2)}\"\n일반 재료: \"{', '.join(remaining_general_ing2)}\"\n공통 재료: \"{', '.join(remaining_common_ing2)}\"\n매우 자주 등장하는 재료: \"{', '.join(remaining_very_common_ing2)}\"",
            },
            {
                "instruction": f"{side_info['food_typ_nm']} 카테고리에 속하는 {k}의 레시피에서 몇 가지 재료가 제외되었습니다. 어떤 재료가 빠졌는지 맞춰보세요.",
                "input": f"핵심 재료: \"{', '.join(remaining_core_ing3)}\"\n일반 재료: \"{', '.join(remaining_general_ing3)}\"\n공통 재료: \"{', '.join(remaining_common_ing3)}\"\n매우 자주 등장하는 재료: \"{', '.join(remaining_very_common_ing3)}\"",
            },
            {
                "instruction": f"{side_info['food_typ_nm']} 카테고리의 {k}에 사용되는 몇 가지 재료입니다. 누락된 재료를 찾아보세요.",
                "input": f"핵심 재료: \"{', '.join(remaining_core_ing4)}\"\n일반 재료: \"{', '.join(remaining_general_ing4)}\"\n공통 재료: \"{', '.join(remaining_common_ing4)}\"\n매우 자주 등장하는 재료: \"{', '.join(remaining_very_common_ing4)}\"",
            }
        ]
        
        answers = [
            ', '.join(excluded1),
            ', '.join(excluded2),
            ', '.join(excluded3),
            ', '.join(excluded4),
        ]
        
        # 각 질문 형식을 리스트에 추가
        for question, answer in zip(questions, answers):
            qa_list.append({
                "QUESTION": question,
                "ANSWER": answer
            })
    
    return qa_list

# 변환된 데이터
qa_dataset = transform_dict_to_qa_format(item_mat_dict, side_info_dict)

# JSON 문자열로 변환
json_result = json.dumps(qa_dataset, indent=4, ensure_ascii=False)

# 결과 출력
print(json_result)




[
    {
        "QUESTION": {
            "instruction": "생면주정처리제품 카테고리의 '23김치생수제비의 식재료의 일부입니다. 빠진 식재료를 맞추세요.",
            "input": "핵심 재료: \"참깨김후레이크\"\n일반 재료: \"생생김치건더기\"\n공통 재료: \"\"\n매우 자주 등장하는 재료: \"밀글루텐, 변성전분sa2, 산미료p, 정제소금\""
        },
        "ANSWER": "수제비소스, 알파메밀분ot, 밀가루, 주정, 변성전분pn"
    },
    {
        "QUESTION": {
            "instruction": "생면주정처리제품 카테고리에 속하는 '23김치생수제비의 일부 재료가 주어졌습니다. 나머지 식재료를 추측해보세요.",
            "input": "핵심 재료: \"수제비소스\"\n일반 재료: \"알파메밀분ot\"\n공통 재료: \"\"\n매우 자주 등장하는 재료: \"변성전분pn, 변성전분sa2, 산미료p, 정제소금\""
        },
        "ANSWER": "참깨김후레이크, 생생김치건더기, 밀가루, 주정, 밀글루텐"
    },
    {
        "QUESTION": {
            "instruction": "생면주정처리제품 카테고리에 속하는 '23김치생수제비의 레시피에서 몇 가지 재료가 제외되었습니다. 어떤 재료가 빠졌는지 맞춰보세요.",
            "input": "핵심 재료: \"참깨김후레이크\"\n일반 재료: \"알파메밀분ot\"\n공통 재료: \"\"\n매우 자주 등장하는 재료: \"밀가루, 변성전분pn, 변성전분sa2, 정제소금\""
        },
        "ANSWER": "수제비소스, 생생김치건더기, 주정, 밀글루텐, 산미료p"
    },
    {
        "QUESTION": {
            "instruction": "생면주정처리제품

In [42]:
qa_dataset

[{'QUESTION': {'instruction': "생면주정처리제품 카테고리의 '23김치생수제비의 식재료의 일부입니다. 빠진 식재료를 맞추세요.",
   'input': '핵심 재료: "참깨김후레이크"\n일반 재료: "생생김치건더기"\n공통 재료: ""\n매우 자주 등장하는 재료: "밀글루텐, 변성전분sa2, 산미료p, 정제소금"'},
  'ANSWER': '수제비소스, 알파메밀분ot, 밀가루, 주정, 변성전분pn'},
 {'QUESTION': {'instruction': "생면주정처리제품 카테고리에 속하는 '23김치생수제비의 일부 재료가 주어졌습니다. 나머지 식재료를 추측해보세요.",
   'input': '핵심 재료: "수제비소스"\n일반 재료: "알파메밀분ot"\n공통 재료: ""\n매우 자주 등장하는 재료: "변성전분pn, 변성전분sa2, 산미료p, 정제소금"'},
  'ANSWER': '참깨김후레이크, 생생김치건더기, 밀가루, 주정, 밀글루텐'},
 {'QUESTION': {'instruction': "생면주정처리제품 카테고리에 속하는 '23김치생수제비의 레시피에서 몇 가지 재료가 제외되었습니다. 어떤 재료가 빠졌는지 맞춰보세요.",
   'input': '핵심 재료: "참깨김후레이크"\n일반 재료: "알파메밀분ot"\n공통 재료: ""\n매우 자주 등장하는 재료: "밀가루, 변성전분pn, 변성전분sa2, 정제소금"'},
  'ANSWER': '수제비소스, 생생김치건더기, 주정, 밀글루텐, 산미료p'},
 {'QUESTION': {'instruction': "생면주정처리제품 카테고리의 '23김치생수제비에 사용되는 몇 가지 재료입니다. 누락된 재료를 찾아보세요.",
   'input': '핵심 재료: "참깨김후레이크"\n일반 재료: "알파메밀분ot"\n공통 재료: ""\n매우 자주 등장하는 재료: "밀가루, 변성전분pn, 변성전분sa2, 주정"'},
  'ANSWER': '수제비소스, 생생김치건더기, 정제소금, 밀글루텐, 산미료p'},
 {'QUES

In [43]:
# JSONL 파일에 저장하는 함수
def save_jsonl_file(file_path, data):
    with open(file_path, 'w', encoding='utf-8') as file:
        for entry in data:
            json_line = json.dumps(entry, ensure_ascii=False)
            file.write(json_line + '\n')

file_path = '/home/jaesung/pulmuone/instruction_tuning_2/v4_completion/data/qa_pair_for_completion.jsonl'

save_jsonl_file(file_path, qa_dataset)

In [44]:
import json 

# JSONL 파일을 로드하는 함수
def load_jsonl_file(file_path):
    data = []
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            json_object = json.loads(line.strip())
            data.append(json_object)
    return data

# JSONL 파일 경로
file_path = '/home/jaesung/pulmuone/instruction_tuning_2/v4_completion/data/qa_pair_for_completion.jsonl'

# JSONL 파일 로드
loaded_data = load_jsonl_file(file_path)

# 결과 출력
print(loaded_data[0])

{'QUESTION': {'instruction': "생면주정처리제품 카테고리의 '23김치생수제비의 식재료의 일부입니다. 빠진 식재료를 맞추세요.", 'input': '핵심 재료: "참깨김후레이크"\n일반 재료: "생생김치건더기"\n공통 재료: ""\n매우 자주 등장하는 재료: "밀글루텐, 변성전분sa2, 산미료p, 정제소금"'}, 'ANSWER': '수제비소스, 알파메밀분ot, 밀가루, 주정, 변성전분pn'}


In [45]:
print(loaded_data[10])

{'QUESTION': {'instruction': "숙면주정처리 카테고리에 속하는 '23물냉면밀키트의 레시피에서 몇 가지 재료가 제외되었습니다. 어떤 재료가 빠졌는지 맞춰보세요.", 'input': '핵심 재료: ""\n일반 재료: "겨자소스, 초절임무우"\n공통 재료: "고구마전분, 도토리가루, 흑미가루"\n매우 자주 등장하는 재료: "소맥분, 정제소금"'}, 'ANSWER': '초절임얼갈이배추, 깔끔한냉면육수, 촉촉삶은계란, 혼합메밀가루, 타피오카조제전분, 주정'}


: 